# Setting up Enviornments

In [26]:
import pandas as pd
import json
import requests
import config
import mysql.connector
from mysql.connector import errorcode

In [73]:
db_name = 'regression_proj'
cnx = mysql.connector.connect(
    host = config.host,
    user = config.user,
    passwd = config.passwd,
    database = db_name
)
cursor = cnx.cursor()

In [8]:
def create_database(cursor, database):
    try:
        cursor.execute(
            "CREATE DATABASE {} DEFAULT CHARACTER SET 'utf8'".format(database))
    except mysql.connector.Error as err:
        print("Failed creating database: {}".format(err))
        exit(1)
try:
    cursor.execute("USE {}".format(db_name))
except mysql.connector.Error as err:
    print("Database {} does not exists.".format(db_name))
    if err.errno == errorcode.ER_BAD_DB_ERROR:
        create_database(cursor, db_name)
        print("Database {} created successfully.".format(db_name))
        cnx.database = db_name
    else:
        print(err)
        exit(1)

Database regression_proj does not exists.
Database regression_proj created successfully.


## Gathering Data

### API call to BreweryDB

In [84]:
def get_brewery_info(url, api_key, page, page_limit):
    """function to pull the information from the Brewery DB API"""
    paged_data = []
    while page <= page_limit:
        url_params = {'key': api_key, 'format':'json', 'p': page, 'withBreweries': 'Y', 'withIngredients': 'Y'}
        response = requests.get(url, params=url_params)
        paged_data.append(response.json())
        page += 1
    return paged_data

In [14]:
api_key = config.key
url_params = {'key': api_key, 'format':'json', 'p': page, 'withBreweries': 'Y', 'withIngredients': 'Y'}
url = "https://sandbox-api.brewerydb.com/v2/beers/"

In [23]:
data = get_brewery_info(url, api_key, 1, 200)

In [52]:
len(data)

200

In [27]:
with open('breweryDB_beer_1_200.json', 'w') as outfile:
    json.dump(data, outfile)

In [121]:
data[7]['data'][0]#['locations']#[0]['established']

{'id': 'CMvItN',
 'name': 'Doppel Weizen',
 'nameDisplay': 'Doppel Weizen',
 'description': "A Brand-Spankin' New Beer Inspired by Rolec: The Builders of our New Brewing System. They Sent Us a Traditional Yeast Sent From Their Friends in Bavaria & We Way-Overfed It To Take It All Up A Bit!",
 'abv': '8.5',
 'glasswareId': 5,
 'styleId': 48,
 'isOrganic': 'N',
 'isRetired': 'N',
 'labels': {'icon': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-icon.png',
  'medium': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-medium.png',
  'large': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-large.png',
  'contentAwareIcon': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-contentAwareIcon.png',
  'contentAwareMedium': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-contentAwareMedium.png',
  'contentAwareLarge': 'https://brewerydb-images.s3.amazonaws.com/beer/CMvItN/upload_zQYlUj-contentAw

In [53]:
for page in data:
    print(page['data'])
#     for deets in item['data']:
#         print(deets)


        beer_id = deets['id']
        beer_name = deets['name']
        beer_abv = deets['abv']
        beer_ibu = deets['ibu']
        beer_style_id = deets['styleId']
        is_organic = deets['isOrganic']
        beer_style = deets['style']['name']
        brewery_name = deets['breweries'][0]['name']
        brewery_est = deets['breweries'][0]['established']
# print(beer_id)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



KeyError: 'data'

In [116]:
def parse(data_lst):
    # elements of the style keys list to look for when we parse through style 
    style_lst = ["id", "name", "shortName",'abvMax','srmMin', 'srmMax', "ibuMax", "ibuMin",
                 'ogMin','fgMin','fgMax' ]
    api_dict_list = []
    # read_through each in the data_list
    for index in range(0,23):
        print(index)
        for api_call in data_lst[index]["data"]:
            api_dict = {}
            api_dict["name"] = api_call["name"]
            if 'abv' in api_call:
                api_dict["abv"] = float(api_call["abv"])
            if 'ibu' in api_call:
                api_dict['ibu'] = float(api_call["ibu"])
            if api_call['isOrganic'] == 'Y':
                api_dict["is_organic"] = 1
            else:
                api_dict['is_organic'] = 0
            api_dict["created"] = api_call["createDate"]
            if "style" in api_call:
                for style in style_lst:
                    if style in api_call["style"]:
                        api_dict[f"style_{style}"] = api_call["style"][style]
                api_dict["category_name"] = api_call["style"]["category"]["name"]
                api_dict["category_id"] = api_call["style"]["category"]["id"]
            brewery = api_call["breweries"][0]
            api_dict[f"brewery_name"] =  brewery["name"]
            api_dict[f"brewery_id"] = brewery["id"]
            if "established" in api_call["breweries"]:
                api_dict[f"established"] = brewery["established"]
            api_dict['location'] = brewery["locations"][0]['region']
#             api_dict["brewery_locations_map"] = []
#             api_dict["brewery_locations"] = []
#             api_dict["brewery_locality"] = ""
#             count = 1
#             for idx in range(len(brewery["locations"])):
#                 brew_location = brewery["locations"][0]
#                 api_dict["brewery_locations"].append(brew_location["name"])
#                 if "latitude" in brew_location and "longitude" in brew_location:
#                     api_dict["brewery_locations_map"].append([float(brew_location["latitude"]),
#                                                              float(brew_location["longitude"])])
#                 if "locality" in brew_location:
#                     api_dict["brewery_locality"]+= f'{count}. {brew_location["locality"]}' + " "
#                     count += 1
#             api_dict["number_of_locations"] = len(api_dict["brewery_locations"])
            api_dict_list.append(api_dict)
    return api_dict_list
parsed_data = parse(data)

0
1
2
3
4
5
6


KeyError: 'region'

In [115]:
parsed_data

[{'name': "'Murican Pilsner",
  'abv': 5.5,
  'is_organic': 0,
  'created': '2013-08-19 11:58:12',
  'style_id': 98,
  'style_name': 'American-Style Pilsener',
  'style_shortName': 'American Pilsener',
  'style_abvMax': '6',
  'style_srmMin': '3',
  'style_srmMax': '6',
  'style_ibuMax': '40',
  'style_ibuMin': '25',
  'style_ogMin': '1.045',
  'style_fgMin': '1.012',
  'style_fgMax': '1.018',
  'category_name': 'North American Lager',
  'category_id': 8,
  'brewery_name': 'Sierra Nevada Brewing Company',
  'brewery_id': 'nHLlnK',
  'location': [{'id': 'IaQrxj',
    'name': 'Main Brewery',
    'streetAddress': '1075 East 20th St',
    'locality': 'Chico',
    'region': 'California',
    'postalCode': '95928',
    'phone': '530-893-3520',
    'website': 'http://www.sierranevada.com/',
    'latitude': 39.7246028,
    'longitude': -121.8157154,
    'isPrimary': 'Y',
    'inPlanning': 'N',
    'isClosed': 'N',
    'openToPublic': 'Y',
    'locationType': 'micro',
    'locationTypeDisplay':

In [75]:
cursor.execute("""CREATE TABLE beer(
                beer_name text NOT NULL,
                abv float,
                ibu float,
                is_organic int,
                created datetime,
                style_id int,
                style_name text,
                style_shortName text,
                style_abvMax float,
                style_srmMin float,
                style_ibuMax float,
                style_ibuMin float,
                style_ogMin float,
                style_fgMin float,
                style_fgMax float,
                category_name text,
                category_id int,
                brewery_name text,
                brewery_id text)""")
cnx.commit()

In [76]:
beer_df = pd.DataFrame(parsed_data)
beer_df.head()

abv brewery_id                   brewery_name  category_id  \
0   5.5     nHLlnK  Sierra Nevada Brewing Company          8.0   
1   4.5     nHLlnK  Sierra Nevada Brewing Company          3.0   
2   5.5     nLsoQ9      Lagunitas Brewing Company          3.0   
3   NaN     TMc6H2     SweetWater Brewing Company          1.0   
4  11.0     TMc6H2     SweetWater Brewing Company          3.0   

                category_name              created   ibu  is_organic  \
0        North American Lager  2013-08-19 11:58:12   NaN           0   
1  North American Origin Ales  2016-08-09 14:44:42  35.0           0   
2  North American Origin Ales  2016-08-03 23:25:54  45.0           0   
3         British Origin Ales  2015-04-16 15:44:15   NaN           0   
4  North American Origin Ales  2013-02-24 16:31:05   NaN           0   

                        name style_abvMax style_fgMax style_fgMin  \
0           'Murican Pilsner            6       1.018       1.012   
1                11.5° PLATO          NaN         NaN         NaN   
2              12th Of Never          5.6       1.014       1.008   
3       15th Anniversary Ale          5.8       1.016        1.01   
4  16 So Fine Red Wheat Wine           12       1.032       1.024   

  style_ibuMax style_ibuMin  style_id                     style_name  \
0           40           25      98.0        American-Style Pilsener   
1          NaN          NaN     164.0         Session India Pale Ale   
2           42           30      25.0        American-Style Pale Ale   
3           45           30       5.0           Extra Special Bitter   
4           85           45      35.0  American-Style Wheat Wine Ale   

  style_ogMin    style_shortName style_srmMax style_srmMin  
0       1.045  American Pilsener            6            3  
1         NaN        Session IPA          NaN          NaN  
2       1.044      American Pale           14            6  
3       1.046                ESB           14            8  
4       1.088          Wheatwine           15            8

In [108]:
beer_df.style_shortName.nunique()

121

In [93]:
brewry_id = beer_df.brewery_id.to_list()

In [102]:
len(brewry_id[:20])

20

In [99]:
def get_brewery_beers(api_key, brewery_list):
    """function to pull the information from the Brewery DB API"""
    brewery_data = []
    for brewery in brewry_id:
        url = f"https://sandbox-api.brewerydb.com/v2/brewery/{brewery}/beers"
        url_params = {'key': api_key, 'format':'json', 'withBreweries': 'Y', 'withIngredients': 'Y'}
        response = requests.get(url, params=url_params)
        brewery_data.append(response.json())
    return brewery_data

In [104]:
beers = get_brewery_beers(api_key, brewry_id[0])

KeyboardInterrupt: 

In [98]:
beers

[{'errorMessage': 'The object you requested was not found.',
  'status': 'failure'},
 {'errorMessage': 'The object you requested was not found.',
  'status': 'failure'}]

In [106]:
beer_df.to_csv('brewery_db_info.csv', index=False)

In [109]:
beer_names = beer_df.name.to_list()

In [110]:
beer_names

["'Murican Pilsner",
 '11.5° PLATO',
 '12th Of Never',
 '15th Anniversary Ale',
 '16 So Fine Red Wheat Wine',
 '1794 The Fergal Project',
 '17th Saison',
 '18th Anniversary Belgian Tripel',
 '19 - Golden Belgian Style Ale',
 '1904 American Red Lager',
 '2 x 4',
 '200th Anniversary Export Stout',
 '2017 Beer Camp',
 '20th Anniversary Imperial Hash IPA on Brett',
 '20th Street Ale Citra',
 '20th Street Ale Crystal',
 '20th Street Ale Magnum',
 '21st Anniversary',
 '25th Anniversary',
 '3 Weight',
 "30th Anniversary - Charlie, Fred & Ken's Bock",
 "30th Anniversary - Fritz and Ken's Ale",
 '30th Anniversary - Grand Cru',
 "30th Anniversary - Jack & Ken's Ale",
 "35th Anniversary  - Brewer's Reserve",
 '420 Extra Pale Ale',
 '420 Fest',
 '420 Strain G13 IPA',
 '471 Double IPA - Hull Melon',
 '471 ESB - Extra Special Bitter',
 '471 IPA Barrel Series: Citra',
 '471 IPA Barrel Series: Eureka!',
 '471 IPA. Aggressive Hoppiness',
 '471 Pilsner',
 '471 Small Batch IPA',
 "5 C's IPA",
 '7 Birds',

In [ ]:
rating, score, no_reviews, no_ratings, abv, avail, style, state[0]

In [123]:
cursor.execute("""CREATE TABLE beer_info(
                beer_rating float,
                ba_score float,
                no_reviews int,
                no_ratings int,
                abv float,
                avail text,
                style text,
                state text)""")
cnx.commit()

In [ ]:
stmt = """INSERT INTO album_details(artist, album, genre, label, rating, reviewer, reviewer_position, day, month, year) 
             VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)"""

        cursor.execute(stmt, table_info)
        cnx.commit()